In [1]:
import lightgbm as lgb
from sklearn.model_selection import StratifiedKFold, KFold
from sklearn.metrics import roc_auc_score
import warnings
from sklearn.preprocessing import LabelEncoder
import pandas as pd
import gc
import os
warnings.simplefilter('ignore')

pd.set_option('max_columns', None)
pd.set_option('max_rows', None)

In [45]:
v = 1
seed = 2020

In [22]:
df_feature = pd.read_pickle('feature{}.pkl'.format(v))
df_feature.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21047 entries, 0 to 21046
Columns: 9779 entries, id to target
dtypes: float64(9771), int64(8)
memory usage: 1.5 GB


In [23]:
df_train = df_feature[df_feature.target.notna()].copy()
df_test = df_feature[df_feature.target.isna()].copy()
df_train.shape, df_test.shape

((15280, 9779), (5767, 9779))

In [26]:
df_test.head(5)

id  x_num_70_mean+x_num_5_mean  x_num_70_mean+x_num_6_mean  \
15280   0                   -0.845447                   -0.310733   
15281   1                    0.420644                    1.079009   
15282   2                   -0.969873                   -0.837845   
15283   3                    2.437657                    0.256877   
15284   4                   -0.986543                   -0.880666   

       x_num_70_mean+x_num_7_mean  x_num_70_mean+x_num_8_mean  \
15280                   -0.284220                    0.837253   
15281                    1.043733                    1.109570   
15282                   -0.805710                   -0.879165   
15283                    0.158046                    0.589693   
15284                   -0.882066                    0.621201   

       x_num_70_mean+x_num_9_mean  x_num_70_mean+x_num_11_mean  \
15280                    0.607563                    -0.279718   
15281                    0.784869                     1.030249   
15282                   -0.871680                    -0.786802   
15283                    1.104021                     0.142852   
15284                   -0.359563                    -0.878999   

       x_num_70_mean+x_num_12_mean  x_num_70_mean+x_num_13_mean  \
15280                    -0.275324                    -0.496146   
15281                     1.028025                     0.549937   
15282                    -0.779846                    -0.616481   
15283                     0.145111                    -0.198983   
15284                    -0.871577                    -0.537508   

       x_num_70_mean+x_num_14_mean  x_num_70_mean+x_num_15_mean  \
15280                    -0.247129                    -0.310668   
15281                     0.983938                     1.113754   
15282                    -0.804782                    -0.862187   
15283                     0.117063                     0.326905   
15284                    -0.892863                    -0.875990   

       x_num_70_mean+x_num_16_mean  x_num_70_mean+x_num_17_mean  \
15280                    -0.268306                    -0.304355   
15281                     1.042428                     1.085691   
15282                    -0.775687                    -0.831581   
15283                     0.154511                     0.298279   
15284                    -0.867938                    -0.845858   

       x_num_70_mean+x_num_18_mean  x_num_70_mean+x_num_20_mean  \
15280                    -0.282638                    -0.264779   
15281                     1.058872                     1.086561   
15282                    -0.826631                    -0.780708   
15283                     0.172876                     0.192325   
15284                    -0.927740                    -0.873709   

       x_num_70_mean+x_num_21_mean  x_num_70_mean+x_num_22_mean  \
15280                    -0.272546                    -0.334639   
15281                     1.036004                     0.933648   
15282                    -0.779081                    -0.841366   
15283                     0.149567                     0.117989   
15284                    -0.871178                    -0.881023   

       x_num_70_mean+x_num_23_mean  x_num_70_mean+x_num_24_mean  \
15280                     0.220064                    -0.263411   
15281                    -1.018017                     0.991436   
15282                     0.036645                    -0.802056   
15283                    -1.339001                     0.115077   
15284                     0.003296                    -0.915578   

       x_num_70_mean+x_num_25_mean  x_num_70_mean+x_num_26_mean  \
15280                     0.028314                    -0.274358   
15281                     1.953164                     1.163607   
15282                    -1.207894                    -0.938081   
15283                     0.960561                     0.540027   
15284                    -1.122748                 

In [27]:
ycol = 'target'
feature_names = list(
    filter(lambda x: x not in [ycol, 'id'], df_train.columns))

In [28]:
from feature_selector import FeatureSelector
fs = FeatureSelector(data = df_train[feature_names], labels = df_train[ycol])
fs.identify_zero_importance(task = 'classification', eval_metric = 'auc',
                            n_iterations = 10, early_stopping = True)
fs.identify_low_importance(cumulative_importance = 0.97)
low_importance_features = fs.ops['low_importance']
print('====low_importance_features=====')
print(low_importance_features)
for i in low_importance_features:
    feature_names.remove(i)

Training Gradient Boosting Model

Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[87]	valid_0's auc: 0.853071	valid_0's binary_logloss: 0.252251
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[94]	valid_0's auc: 0.850241	valid_0's binary_logloss: 0.251117
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[94]	valid_0's auc: 0.843517	valid_0's binary_logloss: 0.257409
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[95]	valid_0's auc: 0.849711	valid_0's binary_logloss: 0.254211
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[96]	valid_0's auc: 0.836401	valid_0's binary_logloss: 0.261195
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[142]	valid_0's auc: 0.860392	valid_0's binary_logloss: 0.247807

In [53]:
from sklearn.metrics import precision_score, recall_score
def custom_f1_eval(y_true, y_pred):
    yr = y_pred
    for i in range(len(y_pred)):
        if y_pred[i] >= 0.7:
            yr[i] = 1
        else :
            yr[i] = 0
    precision = precision_score(y_true, yr)
    recall = recall_score(y_true, yr)
    if precision == 0.0 and recall == 0.0:
        f1 = 0.0
    else:
        f1 = (precision * recall) / (0.4 * precision + 0.6 * recall)
    return "f1", f1, True
model = lgb.LGBMClassifier(objective='binary',
                           boosting_type='gbdt',
                           num_leaves=32,
                           max_depth=5,
                           learning_rate=0.01,
                           n_estimators=10000,
                           subsample=0.8,
                           feature_fraction=0.6,
                           reg_alpha=10,
                           reg_lambda=12,
                           random_state=seed,
                           metric = None,
                           is_unbalance=True)

df_oof = df_train[['id',ycol]].copy()
df_oof['prob'] = 0
prediction = df_test[['id']]
prediction['prob'] = 0

kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=seed)
for fold_id, (trn_idx, val_idx) in enumerate(
        kfold.split(df_train[feature_names], df_train[ycol])):
    X_train = df_train.iloc[trn_idx][feature_names]
    Y_train = df_train.iloc[trn_idx][ycol]

    X_val = df_train.iloc[val_idx][feature_names]
    Y_val = df_train.iloc[val_idx][ycol]
    print('\nFold_{} Training ================================\n'.format(
        fold_id + 1))

    lgb_model = model.fit(X_train,
                          Y_train,
                          eval_names=['train', 'valid'],
                          eval_set=[(X_train, Y_train), (X_val, Y_val)],
                          eval_metric=lambda y_true, y_pred: [custom_f1_eval(y_true, y_pred)],
                          verbose=100,
                          early_stopping_rounds=3000)

    pred_val = lgb_model.predict_proba(
        X_val, num_iteration=lgb_model.best_iteration_)[:, 1]

    df_oof.loc[val_idx, 'prob'] = pred_val

    pred_test = lgb_model.predict_proba(
        df_test[feature_names], num_iteration=lgb_model.best_iteration_)[:, 1]
    prediction['prob'] += pred_test / kfold.n_splits

    del lgb_model, pred_val, pred_test, X_train, Y_train, X_val, Y_val
    gc.collect()


Fold_1 Training ================================

Training until validation scores don't improve for 3000 rounds
[100]	train's binary_logloss: 0.335628	train's f1: 0	valid's binary_logloss: 0.361328	valid's f1: 0
[200]	train's binary_logloss: 0.365536	train's f1: 0.441576	valid's binary_logloss: 0.406679	valid's f1: 0.372493
[300]	train's binary_logloss: 0.367812	train's f1: 0.57509	valid's binary_logloss: 0.420883	valid's f1: 0.414952
[400]	train's binary_logloss: 0.354476	train's f1: 0.623578	valid's binary_logloss: 0.418239	valid's f1: 0.421279
[500]	train's binary_logloss: 0.33726	train's f1: 0.661266	valid's binary_logloss: 0.410262	valid's f1: 0.428922
[600]	train's binary_logloss: 0.320151	train's f1: 0.692704	valid's binary_logloss: 0.400886	valid's f1: 0.429293
[700]	train's binary_logloss: 0.30231	train's f1: 0.724759	valid's binary_logloss: 0.391058	valid's f1: 0.426282
[800]	train's binary_logloss: 0.286248	train's f1: 0.757512	valid's binary_logloss: 0.382094	valid's f1: 

[3200]	train's binary_logloss: 0.0907717	train's f1: 0.990393	valid's binary_logloss: 0.305045	valid's f1: 0.352891
[3300]	train's binary_logloss: 0.0876032	train's f1: 0.9913	valid's binary_logloss: 0.30439	valid's f1: 0.347938
[3400]	train's binary_logloss: 0.0846444	train's f1: 0.992209	valid's binary_logloss: 0.303681	valid's f1: 0.348837
[3500]	train's binary_logloss: 0.0819136	train's f1: 0.993575	valid's binary_logloss: 0.303154	valid's f1: 0.349741
Early stopping, best iteration is:
[511]	train's binary_logloss: 0.335645	train's f1: 0.666384	valid's binary_logloss: 0.412467	valid's f1: 0.414478

Fold_3 Training ================================

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
Training until validation scores don't improve for 3000 rounds
[100]	train's binary_logloss: 0.33749	train's f1: 0	valid's binary_logloss: 0.356869	valid's f1: 0
[200]	train's binary_logloss: 0.368605	train's f1: 0.

[2800]	train's binary_logloss: 0.109294	train's f1: 0.984975	valid's binary_logloss: 0.278687	valid's f1: 0.411612
[2900]	train's binary_logloss: 0.104958	train's f1: 0.985873	valid's binary_logloss: 0.277286	valid's f1: 0.414847
[3000]	train's binary_logloss: 0.100917	train's f1: 0.987673	valid's binary_logloss: 0.276039	valid's f1: 0.40708
[3100]	train's binary_logloss: 0.0971796	train's f1: 0.990386	valid's binary_logloss: 0.275115	valid's f1: 0.404804
[3200]	train's binary_logloss: 0.0937673	train's f1: 0.992658	valid's binary_logloss: 0.274349	valid's f1: 0.39356
[3300]	train's binary_logloss: 0.0905233	train's f1: 0.993114	valid's binary_logloss: 0.273453	valid's f1: 0.394619
[3400]	train's binary_logloss: 0.0874423	train's f1: 0.994941	valid's binary_logloss: 0.27264	valid's f1: 0.394619
[3500]	train's binary_logloss: 0.0845838	train's f1: 0.995399	valid's binary_logloss: 0.271983	valid's f1: 0.391187
[3600]	train's binary_logloss: 0.081871	train's f1: 0.995399	valid's binary_lo

In [40]:
auc = roc_auc_score(df_oof[ycol], df_oof['prob'])
print('auc:', auc)

auc: 0.8467786443420533


In [43]:
os.makedirs('sub', exist_ok=True)
prediction.to_csv('sub/xinwangyinhang_{}.csv'.format(auc), index=False)

In [55]:
os.makedirs('prob', exist_ok=True)

prediction.to_csv('prob/sub_lgb{}.csv'.format(v), index=False)
df_oof[['id', 'prob', ycol]].to_csv('prob/oof_lgb{}.csv'.format(v), index=False)

In [41]:
df_oof.head(100)

id  target      prob
0    0     0.0  0.345990
1    1     0.0  0.007791
2    2     1.0  0.704442
3    3     0.0  0.006179
4    4     1.0  0.903839
5    5     1.0  0.670792
6    6     1.0  0.724755
7    7     0.0  0.242553
8    8     0.0  0.531080
9    9     0.0  0.682851
10  10     1.0  0.622072
11  11     1.0  0.602750
12  12     0.0  0.414984
13  13     1.0  0.831157
14  14     1.0  0.948478
15  15     1.0  0.849966
16  16     1.0  0.675542
17  17     0.0  0.325835
18  18     0.0  0.507115
19  19     0.0  0.646072
20  20     0.0  0.634950
21  21     0.0  0.468451
22  22     0.0  0.379764
23  23     0.0  0.218301
24  24     0.0  0.576783
25  25     0.0  0.434406
26  26     0.0  0.584240
27  27     0.0  0.009671
28  28     0.0  0.406085
29  29     0.0  0.016857
30  30     0.0  0.452159
31  31     0.0  0.312849
32  32     0.0  0.238589
33  33     0.0  0.025904
34  34     0.0  0.109358
35  35     0.0  0.398018
36  36     0.0  0.445925
37  37     0.0  0.076377
38  38     0.0  0.045760
39  39     1.0  0.633111
40  40     1.0  0.739396
41  41     1.0  0.678930
42  42     0.0  0.617424
43  43     0.0  0.561747
44  44     0.0  0.078583
45  45     0.0  0.119824
46  46     0.0  0.040937
47  47     0.0  0.171645
48  48     0.0  0.134601
49  49     0.0  0.424907
50  50     0.0  0.003399
51  51     0.0  0.127870
52  52     0.0  0.029006
53  53     0.0  0.037653
54  54     1.0  0.753007
55  55     0.0  0.231210
56  56     0.0  0.300910
57  57     1.0  0.781291
58  58     0.0  0.022649
59  59     0.0  0.028923
60  60     0.0  0.746812
61  61     0.0  0.142044
62  62     0.0  0.015737
63  63     0.0  0.009500
64  64     1.0  0.764864
65  65     0.0  0.014179
66  66     0.0  0.687949
67  67     0.0  0.071709
68  68     0.0  0.090372
69  69     1.0  0.718822
70  70     0.0  0.013449
71  71     1.0  0.892796
72  72     0.0  0.122524
73  73     0.0  0.161690
74  74     0.0  0.138786
75  75     0.0  0.050653
76  76     0.0  0.224812
77  77     1.0  0.430962
78  78     0.0  0.108005
79  79     0.0  0.019137
80  80     1.0  0.303023
81  81     0.0  0.075365
82  82     0.0  0.127263
83  83     0.0  0.084224
84  84     0.0  0.338870
85  85     0.0  0.027611
86  86     0.0  0.008356
87  87     0.0  0.134650
88  88     0.0  0.430087
89  89     0.0  0.633854
90  90     0.0  0.503965
91  91     0.0  0.782410
92  92     0.0  0.792894
93  93     0.0  0.033350
94  94     0.0  0.356405
95  95     1.0  0.753501
96  96     0.0  0.272894
97  97     1.0  0.112718
98  98     1.0  0.365140
99  99     0.0  0.221727

In [37]:
prediction.head()

id      prob
15280   0  0.118229
15281   1  0.163642
15282   2  0.153162
15283   3  0.268018
15284   4  0.090995

In [18]:
round(.501)

1

In [47]:
import xgboost as xgb
model = xgb.XGBClassifier( 
                           max_depth=6,
                           learning_rate=0.01,
                           n_estimators=10000,
                           subsample=0.8,
                           reg_alpha=10,
                           reg_lambda=12,
#                             tree_method='gpu_hist',
                           random_state=seed)

df_oof = df_train[['id', ycol]].copy()
df_oof['prob'] = 0
prediction = df_test[['id']]
prediction['prob'] = 0
df_importance_list = []

kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=seed)
for fold_id, (trn_idx, val_idx) in enumerate(
        kfold.split(df_train[feature_names], df_train[ycol])):
    X_train = df_train.iloc[trn_idx][feature_names]
    Y_train = df_train.iloc[trn_idx][ycol]

    X_val = df_train.iloc[val_idx][feature_names]
    Y_val = df_train.iloc[val_idx][ycol]

    print('\nFold_{} Training ================================\n'.format(
        fold_id + 1))

    lgb_model = model.fit(X_train,
                          Y_train,
                          eval_set=[(X_train, Y_train), (X_val, Y_val)],
                          verbose=100,
                          eval_metric='auc', 
                          early_stopping_rounds=50)

    pred_val = lgb_model.predict_proba(X_val,)[:, 1]
    df_oof.loc[val_idx, 'prob'] = pred_val

    pred_test = lgb_model.predict_proba(df_test[feature_names])[:, 1]
    prediction['prob'] += pred_test / kfold.n_splits

    df_importance = pd.DataFrame({
        'column': feature_names,
        'importance': lgb_model.feature_importances_,
    })
    df_importance_list.append(df_importance)

    del lgb_model, pred_val, pred_test, X_train, Y_train, X_val, Y_val
    gc.collect()


Fold_1 Training ================================

[0]	validation_0-auc:0.74763	validation_1-auc:0.71771
Multiple eval metrics have been passed: 'validation_1-auc' will be used for early stopping.

Will train until validation_1-auc hasn't improved in 50 rounds.
[100]	validation_0-auc:0.84629	validation_1-auc:0.78909
[200]	validation_0-auc:0.88157	validation_1-auc:0.80969
[300]	validation_0-auc:0.89935	validation_1-auc:0.81655
[400]	validation_0-auc:0.91305	validation_1-auc:0.82104
[500]	validation_0-auc:0.92577	validation_1-auc:0.82422
[600]	validation_0-auc:0.93705	validation_1-auc:0.82687
[700]	validation_0-auc:0.94672	validation_1-auc:0.82846
[800]	validation_0-auc:0.95524	validation_1-auc:0.82991
[900]	validation_0-auc:0.96255	validation_1-auc:0.83098
[1000]	validation_0-auc:0.96881	validation_1-auc:0.83181
[1100]	validation_0-auc:0.97422	validation_1-auc:0.83247
[1200]	validation_0-auc:0.97871	validation_1-auc:0.83346
[1300]	validation_0-auc:0.98245	validation_1-auc:0.83412
[1400]

In [49]:
os.makedirs('prob', exist_ok=True)

prediction.to_csv('prob/sub_xgb{}.csv'.format(v), index=False)
df_oof[['id', 'prob', ycol]].to_csv('prob/oof_xgb{}.csv'.format(v), index=False)